# 3 Interactive map

You are an urban safety planner in Japan, and you are analyzing which areas of Japan need extra earthquake reinforcement.  Which areas are both high in population density and prone to earthquakes?



In [1]:
import pandas as pd
import geopandas as gpd

import folium
from folium import Choropleth
from folium.plugins import HeatMap

The function `embed_map()` for displaying interactive maps. It accepts two arguments: the variable containing the map, and the name of the HTML file where the map will be saved.

In [2]:

def embed_map(m, file_name):
    output_path="/tmp/geo"
    from IPython.display import IFrame
    file_path=f"{output_path}/file_name"
    m.save(file_path)
    return IFrame(file_path, width='100%', height='500px')

In [3]:
root_path="/home/pengfei/data_set/kaggle/geospatial/L03"
boundaries_path=f"{root_path}/Plate_Boundaries/Plate_Boundaries.shp"

In [4]:
plate_boundaries = gpd.read_file(boundaries_path)
plate_boundaries['coordinates'] = plate_boundaries.apply(lambda x: [(b,a) for (a,b) in list(x.geometry.coords)], axis='columns')
plate_boundaries.drop('geometry', axis=1, inplace=True)

plate_boundaries.head()

HAZ_PLATES                                         HAZ_PLAT_1  HAZ_PLAT_2  \
0     TRENCH                              SERAM TROUGH (ACTIVE)        6722   
1     TRENCH                                       WETAR THRUST        6722   
2     TRENCH  TRENCH WEST OF LUZON (MANILA TRENCH) NORTHERN ...        6621   
3     TRENCH                                       BONIN TRENCH        9821   
4     TRENCH                                  NEW GUINEA TRENCH        8001   

   Shape_Leng                                        coordinates  
0    5.843467  [(-5.444200361999947, 133.6808931800001), (-5....  
1    1.829013  [(-7.760600482999962, 125.47879802900002), (-7...  
2    6.743604  [(19.817899819000047, 120.09999798800004), (19...  
3    8.329381  [(26.175899215000072, 143.20620700100005), (26...  
4   11.998145  [(0.41880004000006466, 132.8273013480001), (0....

## Q1. Do earthquakes coincide with plate boundaries?

In [5]:
earth_quakes_path=f"{root_path}/earthquakes1970-2014.csv"

earth_quakes=pd.read_csv(earth_quakes_path)
earth_quakes.head()

DateTime  Latitude  Longitude  Depth  Magnitude MagType  \
0  1970/01/04 17:00:40.20    24.139    102.503   31.0        7.5      Ms   
1  1970/01/06 05:35:51.80    -9.628    151.458    8.0        6.2      Ms   
2  1970/01/08 17:12:39.10   -34.741    178.568  179.0        6.1      Mb   
3  1970/01/10 12:07:08.60     6.825    126.737   73.0        6.1      Mb   
4  1970/01/16 08:05:39.00    60.280   -152.660   85.0        6.0      ML   

   NbStations  Gap  Distance  RMS Source       EventID  
0        90.0  NaN       NaN  0.0    NEI  1.970010e+09  
1        85.0  NaN       NaN  0.0    NEI  1.970011e+09  
2        59.0  NaN       NaN  0.0    NEI  1.970011e+09  
3        91.0  NaN       NaN  0.0    NEI  1.970011e+09  
4         0.0  NaN       NaN  NaN     AK           NaN

In [6]:
# Create a base map with plate boundaries
m_1 = folium.Map(location=[35,136], tiles='cartodbpositron', zoom_start=5)
for i in range(len(plate_boundaries)):
    folium.PolyLine(locations=plate_boundaries.coordinates.iloc[i], weight=2, color='black').add_to(m_1)

In [7]:
m_1

In [8]:
# create an earthquake heat map
HeatMap(data=earth_quakes[['Latitude','Longitude']],radius=15).add_to(m_1)

In [9]:
m_1

With the above figure, we can conclude that earthquakes coincide with plate boundaries.

# Q2 Is there a relationship between earthquake depth and proximity to a plate boundary in Japan?

You recently read that the depth of earthquakes tells us [important information](https://www.usgs.gov/faqs/what-depth-do-earthquakes-occur-what-significance-depth?qt-news_science_products=0#qt-news_science_products) about the structure of the earth.  You're interested to see if there are any intereresting global patterns, and you'd also like to understand how depth varies in Japan.

## View earthquake depth on a map

- Let's check the min max of the column depth
- Classify the depth into different categories and assign a color
- Draw a circle for each earthquake with related depth color

In [11]:
max_depth=earth_quakes["Depth"].max()
min_depth=earth_quakes["Depth"].min()

print(f"The min depth is {min_depth}, and the max depth is {max_depth}")

The min depth is 0.0, and the max depth is 688.0


In [12]:
# Create a base map with plate boundaries
m_2 = folium.Map(location=[35,136], tiles='cartodbpositron', zoom_start=5)
for i in range(len(plate_boundaries)):
    folium.PolyLine(locations=plate_boundaries.coordinates.iloc[i], weight=2, color='black').add_to(m_2)

m_2

In [13]:
# This function classifies depth in four categories and attribute them with a unique color
def get_color(depth:int)->str:
    if depth < 50:
        return "forestgreen"
    elif depth < 200:
        return "Yellow"
    elif depth < 500:
        return "darkorange"
    else:
        return "darkred"

In [14]:
# for each row in earth_quakes, draw a circle
for i in range(0,len(earth_quakes)):
    folium.Circle(
        location=[earth_quakes.iloc[i]['Latitude'], earth_quakes.iloc[i]['Longitude']],
        radius=2000,
        color=get_color(earth_quakes.iloc[i]['Depth'])).add_to(m_2)

In [15]:
m_2

In the above figure, we can notice that in the northern half of Japan, it does appear that earthquakes closer to plate boundaries tend to be shallower (and earthquakes farther from plate boundaries are deeper). This pattern is repeated in other locations, such as the western coast of South America. But, it does not hold everywhere (for instance, in China, Mongolia, and Russia).